In [4]:
# This part of code reads RFB sensor data from an RFB text file and processes it into a structured format using pandas.
# Input: Path to the RFB text file.
# Output: A pandas DataFrame containing the processed sensor data.

import pandas as pd

def read_sensor_data(file_path):
    with open(file_path, 'r') as file:
        lines = file.readlines()
    
    # Find the line where data starts
    data_start_index = 0
    for i, line in enumerate(lines):
        if "[Raw Data]" in line:
            data_start_index = i + 1
            break
    
    # Read the data lines into a DataFrame
    data_lines = lines[data_start_index:]
    data = []
    for line in data_lines:
        parts = line.strip().split()
        #print(parts)
        if len(parts) == 7:
            try:
                line_number = int(parts[0])
                time = parts[1]
                tempC = float(parts[2])
                volt = float(parts[3])
                wt = float(parts[4])
                pow = float(parts[5])
                state = int(parts[6])
                data.append([line_number, time, tempC, volt, wt, pow, state])
            except ValueError:
                continue  # Skip lines that can't be parsed
    
    df = pd.DataFrame(data, columns=['Line Number', 'Time', 'Temperature', 'Voltage', 'Weight', 'Power', 'State'])
    #df["Time"]= df["Time"]-min(df["Time"])
    return df




In [6]:
# This part of code reads RFB sensor data from an RFB text file and processes it into a structured format using pandas.
# Input: Path to the RFB text file.
# Output: A pandas DataFrame containing the processed sensor data.

import pandas as pd

def read_sensor_data(file_path):
    with open(file_path, 'r') as file:
        lines = file.readlines()
    
    # Find the line where data starts
    data_start_index = 0
    for i, line in enumerate(lines):
        if "[Raw Data]" in line:
            data_start_index = i + 1
            break
    
    # Read the data lines into a DataFrame
    data_lines = lines[data_start_index:]
    data = []
    for line in data_lines:
        parts = line.strip().split()
        #print(parts)
        if len(parts) == 7:
            try:
                line_number = int(parts[0])
                time = parts[1]
                tempC = float(parts[2])
                volt = float(parts[3])
                wt = float(parts[4])
                pow = float(parts[5])
                state = int(parts[6])
                data.append([line_number, time, tempC, volt, wt, pow, state])
            except ValueError:
                continue  # Skip lines that can't be parsed
    
    df = pd.DataFrame(data, columns=['Line Number', 'Time', 'Temperature', 'Voltage', 'Weight', 'Power', 'State'])
    #df["Time"]= df["Time"]-min(df["Time"])
    return df

# ********************  END Section  *************************

# This code plots sensor data (Voltage, Weight, Power) from RFB files in a specified folder using Plotly.
# Input: Folder path containing RFB files and a list of serial numbers to filter files.
# Output: Interactive plots of Voltage, Weight, and Power over Time.

import itertools
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import os


def find_rfb_files(root_dir, SN=None):
    matching_files = []
    for dirpath, _, filenames in os.walk(root_dir):
        for filename in filenames:
            if SN:
                if any(sn in filename for sn in SN) and filename.endswith(".rfb"):
                    full_path = os.path.join(dirpath, filename)
                    matching_files.append(full_path)
            else:
                if filename.endswith(".rfb"):
                    full_path = os.path.join(dirpath, filename)
                    matching_files.append(full_path)
    return matching_files
# ********************  END Function  *************************

def plot_text_legend(fpath, SN):
    # Function to get test parameters from file name
    fname= os.path.basename(fpath)
    print(fpath)

    # Get target type from folder name
    if ('F28P-LP' in fpath):
        target= 'F28P-LP'
    elif ('Brush-IQC' in fpath):
        target= 'Brush-IQC'
    elif ('Brush-LP' in fpath):
        target= 'Brush-LP'
    else:
        target= 'UnknownTarget'
    
    # Get height from file name
    if 'w1' in fname:
        ht= '2.5'
    elif 'w2' in fname:
        ht= '2.56'
    elif 'w3' in fname:
        ht= '2.62'
    else:
        ht= '2.43'

    # Get repeat number from file name
    repeat_no = fname.split('.')[0][-2:]

    #ftext= SN+'_'+target+'_'+ht+'in'
    ftext= SN+'_'+repeat_no+'_'+ht+'in'
    return ftext
# ********************  END Function  *************************

def plotly_plot2(folder_path, serial_numbers):
    files = find_rfb_files(folder_path, SN=serial_numbers)
    print(files)
    if not files:
        print(f"No files found with serial number '{serial_number}' in folder '{folder_path}'.")
        return

    # Create a Plotly figure
    fig = go.Figure()
    
    # Define a color palette
    color_palette = itertools.cycle([
        "#1f1fb4", '#ff7f0e', "#56d956", '#d62728',
        "#bc67bd", '#8c564b', "#095020", '#7f7f7f',
        '#bcbd22', "#3ac3d2"
    ])
    file_colors = {}

    for file in files:
        print(file)

        #
        #file_path = os.path.join(folder_path, file)
        df = read_sensor_data(file)
        if df.empty:
            print(f"No valid data in file {file}. Skipping.")
            continue

        # Find SN of this file and create legend text: 
        for SNum in serial_numbers:
            if SNum in file:
                SN= SNum
            else:
                SN= "NotFound"
        plot_text= plot_text_legend(file, SN)

        # Convert time to datetime format for plotting
        try:
            df['Time'] = pd.to_datetime(df['Time'], format='%H:%M:%S.%f')
            df['Time']= df['Time']-min(df['Time'])
        except Exception as e:
            print(f"Time parsing error in file {file}: {e}")
            continue

        # Assign a consistent color for this file
        color = next(color_palette)
        file_colors[file] = color

        t_x= df['Time']

        fig.add_trace(go.Scatter(x=df['Time'], y=df['Power'], mode='lines', name=f'{plot_text} - Power', line=dict(color=color)))

    fig.update_layout(
        title='Sensor Data',
        height=900,
        showlegend=True
    )

    fig.update_xaxes(title_text='Time')
    fig.update_yaxes(title_text='Power')

    fig.show()

# Example usage:
# plot_sensor_data('path_to_your_folder', 'serial_number')


In [7]:
data_path= r'C:\work_folder\RFB2\Catheter_testing\20250919_transducer_repeat\20250919_transducer_repeat'

#plot_sensor_data(data_path, '036667')

SNs= ['24603']
plotly_plot2(data_path, SNs)

['C:\\work_folder\\RFB2\\Catheter_testing\\20250919_transducer_repeat\\20250919_transducer_repeat\\24603F28P1r.rfb', 'C:\\work_folder\\RFB2\\Catheter_testing\\20250919_transducer_repeat\\20250919_transducer_repeat\\24603F28P1r1.rfb', 'C:\\work_folder\\RFB2\\Catheter_testing\\20250919_transducer_repeat\\20250919_transducer_repeat\\24603F28P1r2.rfb', 'C:\\work_folder\\RFB2\\Catheter_testing\\20250919_transducer_repeat\\20250919_transducer_repeat\\24603F28P1r3.rfb', 'C:\\work_folder\\RFB2\\Catheter_testing\\20250919_transducer_repeat\\20250919_transducer_repeat\\24603F28P1r4.rfb', 'C:\\work_folder\\RFB2\\Catheter_testing\\20250919_transducer_repeat\\20250919_transducer_repeat\\24603F28P1r5.rfb', 'C:\\work_folder\\RFB2\\Catheter_testing\\20250919_transducer_repeat\\20250919_transducer_repeat\\24603F28P1r6.rfb', 'C:\\work_folder\\RFB2\\Catheter_testing\\20250919_transducer_repeat\\20250919_transducer_repeat\\24603F28P1r7.rfb', 'C:\\work_folder\\RFB2\\Catheter_testing\\20250919_transducer_re

['19316.rfb', '19316w1p.rfb', '19316w2p.rfb', '19316w3p.rfb']


In [13]:
data_path2= r'C:\work_folder\Misc_codes\data\vibration_table_data\sb0729\sb0729'
#plot_sensor_data(data_path, '036667')

SNs= ['036678GraniteBL2','036678GraniteTap']
plotly_plot2(data_path2, SNs)

['036678GraniteBL2-1.RFB', '036678GraniteBL2-2.RFB', '036678GraniteBL2-3.RFB', '036678GraniteTap-1.RFB', '036678GraniteTap-2.RFB', '036678GraniteTap-3.RFB', '036678GraniteTapScDr-1.RFB', '036678GraniteTapScDr-2.RFB', '036678GraniteTapScDr-3.RFB']


In [14]:
data_path2= r'C:\work_folder\Misc_codes\data\vibration_table_data\sb0729\sb0729'
#plot_sensor_data(data_path, '036667')

SNs= ['036678']
plotly_plot2(data_path2, SNs)

['036678BLGranite-1.RFB', '036678BLGranite-2.RFB', '036678BLGranite-3.RFB', '036678GraniteBL2-1.RFB', '036678GraniteBL2-2.RFB', '036678GraniteBL2-3.RFB', '036678GraniteBLwateroff-1.RFB', '036678GraniteBLwateroff-2.RFB', '036678GraniteBLwateroff-3.RFB', '036678GraniteTap-1.RFB', '036678GraniteTap-2.RFB', '036678GraniteTap-3.RFB', '036678GraniteTapScDr-1.RFB', '036678GraniteTapScDr-2.RFB', '036678GraniteTapScDr-3.RFB', '036678GranitewaterOff2-1.RFB', '036678GranitewaterOff2-2.RFB', '036678GranitewaterOff2-3.RFB']
